# Notebook to extract hidden-states and attention heads activations from LSTM model predictions

In [1]:
import os
import glob
import torch
import gc
import numpy as np
import pandas as pd
from tqdm import tqdm
from model import LSTMExtractor
from sklearn.preprocessing import StandardScaler
from numpy import linalg as la
from tokenizer import tokenize
from utils import set_seed
from data import Dictionary
from utils import read_yaml, save_yaml, batchify_text_with_memory_size

In [2]:
def check_folder(path):
    """Create adequate folders if necessary."""
    try:
        if not os.path.isdir(path):
            check_folder(os.path.dirname(path))
            os.mkdir(path)
    except:
        pass

In [3]:
def transform(activations, path, name, run_index, n_layers_hidden=1, hidden_size=300):
    """activations - surprisal - entropy
    """
    assert activations.values.shape[1] == ((n_layers_hidden) * hidden_size + 2)
    indexes = [[index*hidden_size, (index+1)*hidden_size] for index in range(n_layers_hidden)]
    for order in [2]:
        matrices = []
        for index in indexes:
            matrix = activations.values[:, index[0]:index[1]]
            #with_std = True if order=='std' else False
            #scaler = StandardScaler(with_mean=True, with_std=with_std)
            #scaler.fit(matrix)
            #matrix = scaler.transform(matrix)
            if order is not None and order != 'std':
                matrix = matrix / np.mean(la.norm(matrix, ord=order, axis=1))
            matrices.append(matrix)
        matrices = np.hstack(matrices)
        print(matrices.shape)
        matrices = np.hstack([matrices, activations.values[:, -2:]])
        print(matrices.shape)
        new_data = pd.DataFrame(matrices, columns=activations.columns)
        new_path = path + '_norm-' + str(order).replace('np.', '')
        check_folder(new_path)
        new_data.to_csv(os.path.join(new_path, name + '_run{}.csv'.format(run_index + 1)), index=False)


Defining variables:

In [22]:
template = '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/text/english/text_english_run*.txt' # path to text input
language = 'english'

In [23]:
name_template = 'weights_{}_embedding-size-{}_nhid-{}_nlayers-{}_dropout-{}_memory-size-{}_wiki-kristina_english.pt'


In [28]:
rnn_types = ['LSTM'] * 11
ninps = ['650'] * 11
nhids =  ['650'] * 11
nlayers = ['2'] * 11
dropouts =  ['02'] * 11
memory_sizes = [1, 2, 5, 10, 15, 20, 30, 40, 60, 80, 100] #, np.inf
vocab_path = '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/text/english/lstm_training'
config_path_folder = '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/models/LSTM/configs/'
trained_model_folder = '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/derivatives/fMRI/models/english/'
path_to_data = '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations'

In [29]:
#template = '/Users/alexpsq/Code/Parietal/data/text_english_run*.txt' # path to text input
#config_path_folder = '/Users/alexpsq/Code/Parietal/data/configs/'
#trained_model_folder = '/Users/alexpsq/Code/Parietal'
#path_to_data = '/Users/alexpsq/Code/data/stimuli-representations'
#vocab_path = '/Users/alexpsq/Code/data/'

In [30]:
pretrained_lstm_models = [
    trained_model_folder + name_template.format(rnn_type, ninp, nhid, nlayer, dropout, memory_size) for (rnn_type, ninp, nhid, nlayer, dropout, memory_size) in zip(rnn_types, ninps, nhids, nlayers, dropouts, memory_sizes)] # path to the model from which we want to retrieve the activations
infos = [os.path.basename(model).split('_') for model in pretrained_lstm_models]
names = ['_'.join(os.path.basename(model).split('.')[0].split('_')[1:]) for model in pretrained_lstm_models]
config_paths = [os.path.join(config_path_folder, 'config_' + name + '.yml') for name in names]
config_paths = ['_'.join(config.split('_')[:-3]) + '_' + '_'.join(config.split('_')[-2:]) for config in config_paths]
saving_path_folders = [
    os.path.join(path_to_data, '{}/{}_no_correction'.format(language, name)) for name in names]
prediction_types = ['sequential' for i in pretrained_lstm_models]

In [31]:
saving_path_folders

['/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-1_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-2_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-5_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-10_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embed

In [32]:
def get_config(rnn_type='LSTM',
               language='english',
               ntoken=50001,
               ninp=650,
               nhid=650,
               nlayers=2,
               dropout='02',
               memory_size=np.inf,
               tie_weights=False,
               eos_separator='<eos>',
               cuda=True,
               weights_path=None,
               path_to_vocab=None,
               includ_surprisal=True,
               includ_entropy=True,
               parameters=['in', 'forget', 'out', 'c_tilde', 'hidden', 'cell']):
    config_template = {
        'rnn_type': rnn_type,
        'language': language,
        'ntoken': ntoken,
        'ninp': ninp,
        'nhid': nhid,
        'nlayers': nlayers,
        'dropout': int(dropout)/10,
        'memory_size': memory_size,
        'tie_weights': tie_weights,
        'eos_separator': eos_separator,
        'cuda': cuda,
        'weights_path': os.path.join(weights_path, name_template.format(rnn_type, ninp, nhid, nlayers, dropout, 0)).replace('_memory-size-0', ''),
        'path_to_vocab': path_to_vocab,
        'includ_surprisal': includ_surprisal,
        'includ_entropy': includ_entropy,
        'parameters': parameters}
    return config_template


In [33]:
for index, (rnn_type, ninp, nhid, nlayer, dropout, memory_size) in enumerate(zip(rnn_types, ninps, nhids, nlayers, dropouts, memory_sizes)):
    config_template =  get_config(rnn_type=rnn_type,
                                   language='english',
                                   ntoken=50001,
                                   ninp=int(ninp),
                                   nhid=int(nhid),
                                   nlayers=int(nlayer),
                                   dropout=dropout,
                                   memory_size=memory_size,
                                   weights_path=trained_model_folder,
                                   path_to_vocab=vocab_path,
                                 parameters=['hidden'])
    save_yaml(config_template, config_paths[index])

In [34]:
config_template

{'rnn_type': 'LSTM',
 'language': 'english',
 'ntoken': 50001,
 'ninp': 650,
 'nhid': 650,
 'nlayers': 2,
 'dropout': 0.2,
 'memory_size': 100,
 'tie_weights': False,
 'eos_separator': '<eos>',
 'cuda': True,
 'weights_path': '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/derivatives/fMRI/models/english/weights_LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_wiki-kristina_english.pt',
 'path_to_vocab': '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/text/english/lstm_training',
 'includ_surprisal': True,
 'includ_entropy': True,
 'parameters': ['hidden']}

Creating iterator for each run:

In [35]:
paths = sorted(glob.glob(template))

In [36]:
vocab = Dictionary(vocab_path, language)

In [37]:
iterator_list = [tokenize(path, language, train=False, vocab=vocab) for path in paths]

  0%|          | 0/135 [00:00<?, ?it/s]

primeval
boa
constrictor
Boa
constrictors
grownups
boa
constrictor
digesting
boa
constrictor
grownups
grownups
boa
constrictors
Grownups
tiresome
grownups
hasnt
ve
boa
constrictors
primeval
neckties
grownup
readied
grownups
hadn
boa
constrictors
stared
eyed
disobey
Absurd
crossly
didn
doesn
redrew
boa
constrictor
astounded
boa
constrictor
boa
constrictor
indulgently
isn
redid
peal
didn
daydream
ve
ll
Tie
ll
peal
Anywhere
doesn
didn
Grownups
Asteroid
stylishly
grownups
Grownups
grownups
geraniums
wouldn
shrug
Asteroid
grownups
grownups
boa
constrictor
ll
ll
alright


 34%|███▎      | 59/176 [00:00<00:00, 583.31it/s]

ll
grownups
baobabs
isn
didn
baobabs
baobabs
wouldn
baobab
baobab
baobabs
elongates
timidly
sprig
sprig
radish
baobab
baobab
pierces
baobabs
baobabs
baobabs
moralist
baobabs
baobabs
ve
skirting
aren
baobabs
couldn
baobabs
sunsets
sunsets
chuckled
didn
unscrew
frightful
budge
ll
dumbfounded
grownups
smelled
blushed
couldn
isn
ll
ll
wasn
didn
didn
didn
sprouted
sprout
baobab
rumpled
adornment
yawn
woken
presentable
couldn
sweetly
abashed
sprinkling
aren
sweetly
detest
wouldn
Detests
couldn
Humiliated
coughed
shouldn
perfumed
didn
confidences
didn
contrivances


 44%|████▍     | 76/173 [00:00<00:00, 756.22it/s]

...

tamed
aren
bothersome
ll
ll
ll
tamed
sighed
hurrying
ll
ve
tamed
ll
gazed
tames
aren
ll
ll
ll
ve
tamed
ll
ll
ll
aren
tamed
tamed
ve
grumble
tamed
switchman
switchman
rumbling
switchman
switchman
thundered
aren
switchman
Weren
switchman
thundered
aren
switchman
yawning
squashing
switchman
quench
saver
Myself
didn
Myself


  0%|          | 0/207 [00:00<?, ?it/s]

weariness
immensity
feverish
didn
didn
enchantment
trembled
wasn
moaned
weathervane
ve
woken
didn
trembling
shimmer
baobabs
cabbages
baobabs
aren
boa
constrictors
ll
ok
pang
didn
blushed
wasn
blushed
hesitantly
blushed
blush
doesn
wasn
tamed
isn
isn
didn
ll
ll
didn
muffler
moistened
didn
ve
ll
plummeting
ll
couldn
ll
didn
ll
ll
ll
ll


100%|██████████| 207/207 [00:00<00:00, 983.10it/s]

ll
ll
ll
ll
ll
ll
ll
ll
ll
ll
ll
ll
mustn
Snakes
didn
determinedly
ve
ll
ll
ll
ll
ll
ll
ll
ll
couldn
didn
didn
wasn
fasten
Surely
sweetly
ve
Herein
yourselves
grownup
doesn
ll


In [38]:
acc = 0
for i in iterator_list:
    for j in i:
        if 'unk' in j:
            acc+=1
            print(j)

<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk>
<unk

In [39]:
acc

441

## Activation extraction

In [ ]:
for index, config in enumerate(config_paths):
    extractor = LSTMExtractor(config, language, names[index], prediction_types[index], output_hidden_states=True, memory_size=memory_sizes[index])
    print(extractor.name, ' - Extracting activations ...')
    for run_index, iterator in tqdm(enumerate(iterator_list)):
        print("############# Run {} #############".format(run_index))
        activations  = extractor.extract_activations(iterator, language)
        
        transform(
            activations, 
            saving_path_folders[index], 
            'activations', 
            run_index=run_index,
            n_layers_hidden=2,
            hidden_size=650)  
        #activations.to_csv(os.path.join(saving_path_folders[index], 'activations_run{}.csv'.format(run_index + 1)), index=False)
        
        
        

0it [00:00, ?it/s]
0it [00:00, ?it/s]
2it [00:00, 19.43it/s]

LSTM_embedding-size_650_nhid_650_nlayers_2_dropout_02  - Extracting activations ...
############# Run 0 #############



5it [00:00, 20.25it/s]
8it [00:00, 19.92it/s]
11it [00:00, 20.77it/s]
16it [00:00, 25.02it/s]
22it [00:00, 28.57it/s]
26it [00:00, 26.20it/s]
29it [00:01, 25.37it/s]
32it [00:01, 23.79it/s]
36it [00:01, 24.91it/s]
39it [00:01, 23.13it/s]
42it [00:01, 24.64it/s]
46it [00:01, 25.39it/s]
49it [00:01, 25.12it/s]
52it [00:01, 25.94it/s]
56it [00:02, 28.28it/s]
59it [00:02, 25.24it/s]
62it [00:02, 25.89it/s]
65it [00:02, 23.93it/s]
68it [00:02, 23.47it/s]
71it [00:02, 22.62it/s]
75it [00:02, 23.86it/s]
78it [00:03, 24.49it/s]
81it [00:03, 25.85it/s]
84it [00:03, 25.94it/s]
87it [00:03, 24.35it/s]
90it [00:03, 23.12it/s]
93it [00:03, 23.22it/s]
96it [00:03, 24.53it/s]
100it [00:03, 26.86it/s]
104it [00:04, 28.95it/s]
108it [00:04, 29.85it/s]
112it [00:04, 31.02it/s]
117it [00:04, 34.97it/s]
121it [00:04, 29.89it/s]
125it [00:04, 29.21it/s]
130it [00:04, 32.92it/s]
135it [00:04, 36.33it/s]
139it [00:05, 34.63it/s]
143it [00:05, 35.62it/s]
147it [00:05, 33.99it/s]
151it [00:05, 31.02it/s]
155i

(1894, 1300)
(1894, 1302)


1it [00:30, 30.83s/it]
0it [00:00, ?it/s]
6it [00:00, 55.91it/s]

...

39636it [15:40, 36.69it/s]
39640it [15:40, 26.92it/s]
39644it [15:40, 29.53it/s]
39648it [15:40, 32.01it/s]
39652it [15:40, 33.49it/s]
39657it [15:40, 35.28it/s]
39661it [15:40, 33.41it/s]
39665it [15:41, 34.62it/s]
39669it [15:41, 26.16it/s]
39673it [15:41, 28.80it/s]
39677it [15:41, 30.94it/s]
39681it [15:41, 32.58it/s]
39685it [15:41, 34.03it/s]
39689it [15:41, 34.76it/s]
39693it [15:42, 25.77it/s]
39697it [15:42, 28.50it/s]
39701it [15:42, 30.60it/s]
39705it [15:42, 32.59it/s]
39709it [15:42, 33.84it/s]
39713it [15:42, 34.68it/s]
39717it [15:42, 30.30it/s]
39721it [15:43, 25.37it/s]
39725it [15:43, 27.49it/s]
39729it [15:43, 29.99it/s]
39733it [15:43, 32.13it/s]
39737it [15:43, 29.73it/s]
39741it [15:43, 26.19it/s]
39745it [15:43, 29.13it/s]
39749it [15:43, 31.35it/s]
39753it [15:44, 33.17it/s]
39757it [15:44, 34.46it/s]
39761it [15:44, 25.95it/s]
39765it [15:44, 28.60it/s]
39769it [15:44, 30.49it/s]
39773it [15:44, 32.20it/s]
39777it [15:44, 33.42it/s]
39781it [15:44, 32.37it/s]
3

40721it [16:14, 36.48it/s]
40725it [16:14, 37.35it/s]
40729it [16:14, 37.40it/s]
40734it [16:14, 38.17it/s]
40738it [16:14, 37.90it/s]
40742it [16:15, 35.35it/s]
40746it [16:15, 36.42it/s]
40750it [16:15, 36.66it/s]
40754it [16:15, 37.05it/s]
40758it [16:15, 37.56it/s]
40762it [16:15, 37.98it/s]
40766it [16:15, 38.44it/s]
40770it [16:15, 38.28it/s]
40775it [16:15, 38.69it/s]
40779it [16:16, 37.91it/s]
40783it [16:16, 37.64it/s]
40787it [16:16, 38.00it/s]
40792it [16:16, 39.21it/s]
40796it [16:16, 38.81it/s]
40800it [16:16, 38.78it/s]
40804it [16:16, 35.67it/s]
40808it [16:16, 36.51it/s]
40812it [16:16, 37.28it/s]
40816it [16:17, 37.79it/s]
40821it [16:17, 40.41it/s]
40826it [16:17, 39.37it/s]
40830it [16:17, 38.22it/s]
40834it [16:17, 38.11it/s]
40838it [16:17, 38.40it/s]
40842it [16:17, 37.96it/s]
40847it [16:17, 39.49it/s]
40851it [16:17, 39.03it/s]
40855it [16:17, 38.71it/s]
40859it [16:18, 38.20it/s]
40863it [16:18, 35.67it/s]
40868it [16:18, 36.77it/s]
40873it [16:18, 38.91it/s]
4

41867it [16:44, 38.16it/s]
41871it [16:44, 38.03it/s]
41876it [16:44, 40.22it/s]
41881it [16:44, 37.38it/s]
41885it [16:44, 37.66it/s]
41889it [16:45, 38.02it/s]
41893it [16:45, 38.29it/s]
41898it [16:45, 39.57it/s]
41902it [16:45, 39.31it/s]
41906it [16:45, 39.19it/s]
41910it [16:45, 35.88it/s]
41914it [16:45, 35.79it/s]
41918it [16:45, 36.37it/s]
41922it [16:45, 36.84it/s]
41926it [16:46, 37.03it/s]
41930it [16:46, 37.50it/s]
41934it [16:46, 38.16it/s]
41939it [16:46, 39.61it/s]
41943it [16:46, 36.14it/s]
41947it [16:46, 36.68it/s]
41951it [16:46, 36.79it/s]
41955it [16:46, 37.14it/s]
41959it [16:46, 37.59it/s]
41963it [16:47, 37.66it/s]
41967it [16:47, 37.50it/s]
41971it [16:47, 37.66it/s]
41975it [16:47, 38.04it/s]
41979it [16:47, 37.83it/s]
41983it [16:47, 38.13it/s]
41987it [16:47, 38.35it/s]
41991it [16:47, 37.62it/s]
41995it [16:47, 37.61it/s]
42000it [16:48, 39.27it/s]
42004it [16:48, 36.32it/s]
42008it [16:48, 36.69it/s]
42012it [16:48, 37.25it/s]
42016it [16:48, 36.95it/s]
4

43007it [17:14, 38.95it/s]
43011it [17:14, 38.96it/s]
43015it [17:14, 38.84it/s]
43019it [17:14, 38.79it/s]
43023it [17:14, 34.92it/s]
43027it [17:14, 35.71it/s]
43031it [17:15, 36.86it/s]
43035it [17:15, 37.04it/s]
43039it [17:15, 37.67it/s]
43043it [17:15, 37.62it/s]
43047it [17:15, 37.24it/s]
43051it [17:15, 37.80it/s]
43055it [17:15, 37.75it/s]
43059it [17:15, 37.86it/s]
43063it [17:15, 37.91it/s]
43067it [17:15, 37.83it/s]
43071it [17:16, 37.97it/s]
43075it [17:16, 38.36it/s]
43080it [17:16, 39.70it/s]
43084it [17:16, 36.46it/s]
43088it [17:16, 36.84it/s]
43092it [17:16, 37.25it/s]
43096it [17:16, 37.24it/s]
43101it [17:16, 38.87it/s]
43105it [17:16, 38.51it/s]
43109it [17:17, 38.50it/s]
43113it [17:17, 38.45it/s]
43117it [17:17, 38.23it/s]
43121it [17:17, 38.49it/s]
43125it [17:17, 38.58it/s]
43129it [17:17, 38.27it/s]
43133it [17:17, 38.50it/s]
43137it [17:17, 38.38it/s]
43141it [17:17, 35.38it/s]
43145it [17:18, 36.17it/s]
43149it [17:18, 37.08it/s]
43153it [17:18, 37.49it/s]
4

44119it [17:43, 37.40it/s]
44124it [17:43, 38.21it/s]
44128it [17:44, 38.35it/s]
44133it [17:44, 39.53it/s]
44137it [17:44, 38.74it/s]
44141it [17:44, 39.08it/s]
44145it [17:44, 38.96it/s]
44149it [17:44, 38.45it/s]
44153it [17:44, 37.97it/s]
44157it [17:44, 38.29it/s]
44161it [17:44, 35.68it/s]
44165it [17:44, 36.47it/s]
44169it [17:45, 37.05it/s]
44176it [17:45, 41.33it/s]
44181it [17:45, 40.31it/s]
44186it [17:45, 41.31it/s]
44191it [17:45, 40.62it/s]
44196it [17:45, 39.83it/s]
44201it [17:45, 39.44it/s]
44205it [17:45, 38.97it/s]
44209it [17:46, 38.82it/s]
44213it [17:46, 38.86it/s]
44217it [17:46, 38.92it/s]
44221it [17:46, 36.00it/s]
44225it [17:46, 36.65it/s]
44229it [17:46, 36.93it/s]
44233it [17:46, 37.02it/s]
44237it [17:46, 37.69it/s]
44241it [17:46, 37.87it/s]
44245it [17:47, 37.73it/s]
44249it [17:47, 37.71it/s]
44253it [17:47, 37.97it/s]
44257it [17:47, 37.67it/s]
44261it [17:47, 37.60it/s]
44265it [17:47, 37.67it/s]
44269it [17:47, 37.52it/s]
44273it [17:47, 37.42it/s]
4

In [41]:
saving_path_folders

['/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-1_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-2_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-5_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embedding-size-650_nhid-650_nlayers-2_dropout-02_memory-size-10_wiki-kristina_english_no_correction',
 '/neurospin/unicog/protocols/IRMf/LePetitPrince_Pallier_2018/LePetitPrince/data/stimuli-representations/english/LSTM_embed

In [50]:
activations.values.shape

(1894, 1302)